In [3]:
#------------------------------------------------------------------#
# The following main is intended to give an example of calculations
# performed over the data of an asset
#------------------------------------------------------------------#

import sys
sys.path.append('./trading_libraries')

In [4]:
from asset_library import initialize_data
from plot_library import plot_candlestick_chart

#---------------------------------------------------------#
# Choose the asset to download
# - Use the asset name you want, below some examples
#---------------------------------------------------------#
# Examples = 
# 'ISP.MI' | 'ADB.MI'  | 'ENI.MI' | 'US.MI' | 'GOOG' | 'STMMI.MI'
# 'SPOT'   | 'CNHI.MI' | 'MSFT'   | '^FCHI'
ticker = 'MCHP'    # Microchip

#---------------------------------------------------------#
# Initialize the data:
# 1) Download it from yahoo finance
# 2) Compute adjusted prices
#
# The final structure is a Pandas DataFrame with following
# fields:
# Date | Open | Close | High | Low | Volume | Adj Open | Adj Close | Adj High | Adj Low
#---------------------------------------------------------#
asset = initialize_data( ticker )

#---------------------------------------------------------#
# Plot candlestick chart with adjusted prices
#---------------------------------------------------------#
plot_candlestick_chart( asset , ticker )

[*********************100%***********************]  1 of 1 completed


In [5]:
from ta import trend
from ta import volatility
from asset_library import Trailing_SL_Indicator
from plot_library import plot_chart_indicators

#---------------------------------------------------------#
# Compute and plot indicators
#---------------------------------------------------------#

#---------------------------------------------------------#
# Here only a small subset of indicators are calculated
# as an example:
#   - EMA fast        (Exponential Moving Average)
#   - EMA slow
#   - Bollinger bands
#   - MACD 12/26/9    (Moving Average Convergence/Divergence)
#   - ATR             (Average True Range)
#---------------------------------------------------------#
# EMA
EMA_fast = trend.EMAIndicator( asset['Adj Close'] , 60  , False )
EMA_slow = trend.EMAIndicator( asset['Adj Close'] , 250 , False )
# Bollinger bands
BB = volatility.BollingerBands ( asset['Adj Close'] , window = 50 , window_dev = 2 )
# MACD 12/26/9
MACD = trend.MACD( asset['Adj Close'] , 26 , 12 , 9 , False )
# ATR
ATR = volatility.AverageTrueRange( asset['Adj High'] , asset['Adj Low'] , asset['Adj Close'] , 14 , False )

#---------------------------------------------------------#
# For facilitate the usage, the indicators are added to
# the asset dataframe as new columns
# 
# EMA_fast | EMA_slow | BB_high | BB_low | ATR
#---------------------------------------------------------#
asset['EMA_fast']    = EMA_fast.ema_indicator( )
asset['EMA_slow']    = EMA_slow.ema_indicator( )
asset['BB_high']     = BB.bollinger_hband( )
asset['BB_low']      = BB.bollinger_lband( )
asset['MACD']        = MACD.macd( )
asset['MACD_signal'] = MACD.macd_signal( )
asset['MACD_H']      = MACD.macd_diff( )
asset['ATR']         = ATR.average_true_range( )

#---------------------------------------------------------#
# Compute the derived indicator "Trailing Stop-Loss"
#---------------------------------------------------------#
asset['Trailing SL'] = Trailing_SL_Indicator( asset['Adj Close'] , asset['ATR'] , 2 )

#---------------------------------------------------------#
# Plot a chart with all the computed indicators
#---------------------------------------------------------#
plot_chart_indicators( asset , ticker )

In [6]:
import datetime as datetime
from asset_library import reduce_asset

#---------------------------------------------------------#
# Select a desired time interval to which focus the 
# analysis
#---------------------------------------------------------#
start_date = datetime.date(2018,1,1)
end_date   = datetime.date(2023,8,18)

asset_red = reduce_asset( asset , start_date , end_date )

#---------------------------------------------------------#
# Plot reduced candlestick chart with adjusted prices
#---------------------------------------------------------#
plot_chart_indicators( asset , ticker )

In [10]:
from pymle.models.CKLS import CKLS
from pymle.core.TransitionDensity import *
from pymle.fit.AnalyticalMLE import AnalyticalMLE
from pymle.sim.Simulator1D import Simulator1D
from estimation_library import lasso_estimation
import numpy as np

#---------------------------------------------------------#
# Use maximum likelihood estimation to estimate the
# parameters of CKLS stochastic process to represent the 
# evolution of the asset
#---------------------------------------------------------#

#--------------------------------------------------------------#
# Create the Hypothesized model (CKLS)
#--------------------------------------------------------------#
model        = CKLS()

alpha_min = -10.0; beta_min = -10.0; sigma_min = -10.0; gamma_min = -10.0#0.501
alpha_max = 10.0; beta_max = 10.0; sigma_max = 10.0; gamma_max = 10.0
param_bounds = [(alpha_min,alpha_min) , (beta_min,beta_max) , (sigma_min,sigma_max), (gamma_min,gamma_max)]  # bounds for param search

guess        = np.array([1, -1, 1, 0.6])  # Some guess for the params

skip   = 1            # sample rate: 1 = 1 day, 20 = 20 days (almost 1 month), etc.
freq   = 252.          # observations per year
dt     = skip / freq
sample = asset_red['Adj Close'].values[0:-1:skip]

#--------------------------------------------------------------#
# Fit maximum Likelihood estimators
#--------------------------------------------------------------#
# Fit using Euler MLE
print("\nStarting Euler------------------\n")
euler_est = AnalyticalMLE(sample=sample, param_bounds=param_bounds, dt=dt,
                            density=EulerDensity(model)).estimate_params(guess)
print(f'\nEuler MLE: {euler_est.params} \n')

# Second step - LASSO model selection
alpha_0 = 3; beta_0  = 3; sigma_0 = 3; gamma_0 = 3
delta_1 = 1; delta_2 = 1; delta_3 = 1;  delta_4 = 1

penalties = np.array( [ alpha_0 , beta_0 , sigma_0 , gamma_0 ] )
delta = np.array( [ delta_1 , delta_2, delta_3 , delta_4 ] )

theta_min = np.array( [ alpha_min , beta_min , sigma_min , gamma_min ] )
theta_max = np.array( [ alpha_max , beta_max , sigma_max , gamma_max ] )

lasso_res = lasso_estimation( sample , dt , euler_est.params , euler_est.params , theta_min , theta_max , penalties , delta )
theta_lasso = np.array( [ lasso_res.x[0] , lasso_res.x[1] , lasso_res.x[2] , lasso_res.x[3] ] )
print(f'\nLasso refinement: {theta_lasso} \n')


Starting Euler------------------

Initial Params: [ 1.  -1.   1.   0.6]
Initial Likelihood: -3889.8801510250482
`gtol` termination condition is satisfied.
Number of iterations: 70, function evaluations: 320, CG iterations: 154, optimality: 3.31e-07, constraint violation: 1.78e-15, execution time: 0.12 s.
Final Params: [-10.           0.3054261    2.48397353   0.55479847]
Final Likelihood: -2511.6981006610613

Euler MLE: [-10.           0.3054261    2.48397353   0.55479847] 

`xtol` termination condition is satisfied.
Number of iterations: 150, function evaluations: 945, CG iterations: 397, optimality: 1.45e+00, constraint violation: 0.00e+00, execution time: 0.16 s.

Lasso refinement: [-1.13235684e-09  1.66764836e-07  2.39159404e+00  5.63882996e-01] 



c:\Users\marco\AppData\Local\Programs\Python\Python312\Lib\site-packages\scipy\optimize\_differentiable_functions.py:316: UserWarning:

delta_grad == 0.0. Check if the approximated function is linear. If the function is linear better results can be obtained by defining the Hessian as zero instead of using quasi-Newton approximations.



In [8]:
from stochastic_library import Montecarlo_simulation
from trdg_library import *

#--------------------------------------------------------------#
# Montecarlo simulation and Stochastic MPC implementation
#--------------------------------------------------------------#

#--------------------------------------------------------------#
# Montecarlo simulation of CKLS stochastic process with 
# parameters estimated from selected asset data
#--------------------------------------------------------------#
theta_esti = euler_est.params
S0   = asset_red['Adj Close'].values[-1]  # initial value of process
T    = 200    # num of days of the sample
dt   = 1. / freq
seed = None  # random seed: set to None to get new results each time

model_sim = CKLS()
model_sim.params = np.round(theta_esti,3)

nr_of_sim = 500

sims = Montecarlo_simulation( S0 , T , dt , model_sim , nr_of_sim , seed )

#--------------------------------------------------------------#
# SMPC run with simulated paths
#--------------------------------------------------------------#
horizon_length     = 20                                  # 1 = 1 day if delta_t = 1, 1 = 5 days if delta_t = 5, etc.
risk_free_fact     = 0
inv_limit          = 1.0                            # it must be 0 <= inv_limit <= 1
risk_aversion_coef = 0.05

V0 = 1000                                           # initial account value

u = SMPC_control( horizon_length , nr_of_sim , sims , V0 , risk_free_fact , risk_aversion_coef , inv_limit , 'l' )

V_exp  = account_expected_value( horizon_length , nr_of_sim , sims , V0 , risk_free_fact , u )

print( 'Investment level: ' + str(u) )
print( 'Investment: ' + str(np.round( u*S0 , 3 )) + '$' )
print( 'Expected account value: ' + str(V_exp) )
print( 'Expected gain: ' + str(100*(V_exp-V0)/V0) )

Investment level: 0.27
Investment: 20.891$
Expected account value: 1000.235
Expected gain: 0.023500000000001364


In [9]:
from asset_library import asset_search_for_date

#--------------------------------------------------------------#
# Check the result of the SMPC control with the data of the 
# complete asset
#
# NOTES: the proposed strategy is supposed for a single run
#        meaning that as soos as an exit condition is detected
#        the strategy stops --> it is not "iterative"
#--------------------------------------------------------------#
start_idx = asset_search_for_date( asset , end_date )
stop_idx  = asset_search_for_date( asset , end_date + datetime.timedelta(days=20) )

exit_flag = False
day_idx = start_idx
while ( exit_flag == False ) and ( day_idx < stop_idx ):

    # stop loss
    stop_price = asset['Adj Close'].iloc[day_idx+1]

    if ( u > 0 ):
        if ( asset['Adj Low'].iloc[day_idx+1] < asset['Trailing SL'].iloc[day_idx] ):
            stop_price = asset['Trailing SL'].iloc[day_idx]
            exit_flag = True
    elif ( u < 0 ):
        if ( asset['Adj High'].iloc[day_idx+1] > asset['Trailing SL'].iloc[day_idx] ):
            stop_price = asset['Trailing SL'].iloc[day_idx]
            exit_flag = True

    day_idx += 1

print( 'Investment level: ' + str(u) )
print( 'Investment: ' + str(np.round( u*S0 , 3 )) + '$' )

print( 'Target stop day: ' + str(stop_idx) )
print( 'Effective stop day: ' + str(day_idx) )

delta_price = stop_price - (1+risk_free_fact)*S0
print( 'Starting asset price: ' + str(S0) )
print( 'Stopping price: ' + str(stop_price) )

print( 'Expected account value: ' + str(V_exp) )

V_update = np.round( V0*(1+risk_free_fact) + u*delta_price , 3 )
print( 'Final account value: ' + str(V_update) )

print( 'Gain/Loss %: ' + str( np.round( 100*(V_update-V0)/V0 , 3 ) ) )

Investment level: 0.27
Investment: 20.891$
Target stop day: 7672
Effective stop day: 7660
Starting asset price: 77.374
Stopping price: 81.754
Expected account value: 1000.235
Final account value: 1001.183
Gain/Loss %: 0.118
